# Fine-tuning a model for Mental Illness Prediction (with the Trainer API or Keras)

Install the Transformers, Datasets, and Evaluate libraries to run this notebook.

In [107]:
!pip install datasets evaluate transformers[sentencepiece]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [8]:
from datasets import load_dataset
from transformers import AutoTokenizer, DataCollatorWithPadding
import numpy as np

from datasets import load_dataset
raw_datasets = load_dataset("dreaddit-train.csv")
raw_datasets

FileNotFoundError: ignored

In [72]:
import pandas as pd
df=pd.read_csv('dreaddit-train.csv')
df.shape

(2838, 116)

In [73]:
subreddit = df["subreddit"]
subreddit

text_subreddit = df[["text", "subreddit"]]
text_subreddit

text         subreddit
0     He said he had not felt that way before, sugge...              ptsd
1     Hey there r/assistance, Not sure if this is th...        assistance
2     My mom then hit me with the newspaper and it s...              ptsd
3     until i met my new boyfriend, he is amazing, h...     relationships
4     October is Domestic Violence Awareness Month a...  survivorsofabuse
...                                                 ...               ...
2833  * Her, a week ago: Precious, how are you? (I i...     relationships
2834  I don't have the ability to cope with it anymo...              ptsd
2835  In case this is the first time you're reading ...           anxiety
2836  Do you find this normal? They have a good rela...    almosthomeless
2837  I was talking to my mom this morning and she s...              ptsd

[2838 rows x 2 columns]

In [74]:
df.subreddit.unique()

array(['ptsd', 'assistance', 'relationships', 'survivorsofabuse',
       'domesticviolence', 'anxiety', 'homeless', 'stress',
       'almosthomeless', 'food_pantry'], dtype=object)

In [88]:
x=list(df['text'])
y=list(df['subreddit'])

In [89]:
x

['He said he had not felt that way before, suggeted I go rest and so ..TRIGGER AHEAD IF YOUI\'RE A HYPOCONDRIAC LIKE ME: i decide to look up "feelings of doom" in hopes of maybe getting sucked into some rabbit hole of ludicrous conspiracy, a stupid "are you psychic" test or new age b.s., something I could even laugh at down the road. No, I ended up reading that this sense of doom can be indicative of various health ailments; one of which I am prone to.. So on top of my "doom" to my gloom..I am now f\'n worried about my heart. I do happen to have a physical in 48 hours.',
 "Hey there r/assistance, Not sure if this is the right place to post this.. but here goes =) I'm currently a student intern at Sandia National Labs and working on a survey to help improve our marketing outreach efforts at the many schools we recruit at around the country. We're looking for current undergrad/grad STEM students so if you're a STEM student or know STEM students, I would greatly appreciate if you can help

In [92]:
y

['ptsd',
 'assistance',
 'ptsd',
 'relationships',
 'survivorsofabuse',
 'relationships',
 'domesticviolence',
 'anxiety',
 'relationships',
 'assistance',
 'anxiety',
 'anxiety',
 'anxiety',
 'homeless',
 'anxiety',
 'relationships',
 'anxiety',
 'domesticviolence',
 'assistance',
 'relationships',
 'domesticviolence',
 'survivorsofabuse',
 'ptsd',
 'ptsd',
 'survivorsofabuse',
 'ptsd',
 'anxiety',
 'assistance',
 'relationships',
 'anxiety',
 'ptsd',
 'stress',
 'domesticviolence',
 'assistance',
 'homeless',
 'anxiety',
 'survivorsofabuse',
 'relationships',
 'domesticviolence',
 'ptsd',
 'anxiety',
 'anxiety',
 'assistance',
 'anxiety',
 'anxiety',
 'ptsd',
 'domesticviolence',
 'assistance',
 'homeless',
 'domesticviolence',
 'relationships',
 'ptsd',
 'ptsd',
 'domesticviolence',
 'domesticviolence',
 'relationships',
 'ptsd',
 'anxiety',
 'ptsd',
 'ptsd',
 'survivorsofabuse',
 'ptsd',
 'anxiety',
 'anxiety',
 'anxiety',
 'ptsd',
 'relationships',
 'assistance',
 'anxiety',
 'sur

In [101]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
le.fit(y)
list(le.classes_)
y_labeled=le.transform(y)
list(y_labeled)

[6,
 2,
 6,
 7,
 9,
 7,
 3,
 1,
 7,
 2,
 1,
 1,
 1,
 5,
 1,
 7,
 1,
 3,
 2,
 7,
 3,
 9,
 6,
 6,
 9,
 6,
 1,
 2,
 7,
 1,
 6,
 8,
 3,
 2,
 5,
 1,
 9,
 7,
 3,
 6,
 1,
 1,
 2,
 1,
 1,
 6,
 3,
 2,
 5,
 3,
 7,
 6,
 6,
 3,
 3,
 7,
 6,
 1,
 6,
 6,
 9,
 6,
 1,
 1,
 1,
 6,
 7,
 2,
 1,
 9,
 8,
 6,
 6,
 7,
 6,
 7,
 5,
 1,
 2,
 6,
 9,
 2,
 7,
 7,
 1,
 9,
 2,
 7,
 2,
 7,
 1,
 2,
 7,
 1,
 8,
 1,
 1,
 3,
 3,
 3,
 2,
 6,
 9,
 6,
 6,
 6,
 1,
 1,
 7,
 3,
 7,
 6,
 5,
 2,
 1,
 6,
 6,
 3,
 7,
 1,
 6,
 6,
 5,
 1,
 2,
 7,
 7,
 8,
 7,
 7,
 6,
 1,
 1,
 7,
 2,
 3,
 7,
 7,
 7,
 1,
 3,
 0,
 6,
 3,
 1,
 6,
 1,
 6,
 7,
 6,
 2,
 7,
 5,
 1,
 6,
 4,
 7,
 5,
 3,
 1,
 1,
 1,
 6,
 6,
 3,
 7,
 1,
 7,
 7,
 7,
 9,
 2,
 2,
 7,
 3,
 7,
 7,
 1,
 7,
 1,
 6,
 9,
 4,
 6,
 1,
 5,
 7,
 3,
 0,
 5,
 1,
 3,
 1,
 9,
 3,
 2,
 2,
 6,
 6,
 6,
 2,
 3,
 1,
 5,
 7,
 1,
 3,
 5,
 1,
 9,
 6,
 1,
 3,
 6,
 3,
 6,
 1,
 5,
 1,
 1,
 1,
 6,
 3,
 2,
 1,
 1,
 3,
 9,
 1,
 7,
 1,
 6,
 6,
 2,
 1,
 7,
 3,
 7,
 7,
 3,
 7,
 7,
 6,
 6,
 3,
 6,
 5,
 6,
 7,
 8,


In [102]:
y_labelled=list(pd.get_dummies(y,drop_first=True))
y_labelled

['anxiety',
 'assistance',
 'domesticviolence',
 'food_pantry',
 'homeless',
 'ptsd',
 'relationships',
 'stress',
 'survivorsofabuse']

In [103]:
from transformers import DistilBertTokenizerFast
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

In [104]:
train_encodings = tokenizer(x, truncation=True, padding=True)

In [106]:
train_encodings

{'input_ids': [[101, 2002, 2056, 2002, 2018, 2025, 2371, 2008, 2126, 2077, 1010, 10514, 13871, 12870, 2094, 1045, 2175, 2717, 1998, 2061, 1012, 1012, 9495, 3805, 2065, 2017, 2072, 1005, 2128, 1037, 1044, 22571, 24163, 4859, 4360, 2278, 2066, 2033, 1024, 1045, 5630, 2000, 2298, 2039, 1000, 5346, 1997, 12677, 1000, 1999, 8069, 1997, 2672, 2893, 8631, 2046, 2070, 10442, 4920, 1997, 11320, 14808, 13288, 9714, 1010, 1037, 5236, 1000, 2024, 2017, 12663, 1000, 3231, 2030, 2047, 2287, 1038, 1012, 1055, 1012, 1010, 2242, 1045, 2071, 2130, 4756, 2012, 2091, 1996, 2346, 1012, 2053, 1010, 1045, 3092, 2039, 3752, 2008, 2023, 3168, 1997, 12677, 2064, 2022, 24668, 1997, 2536, 2740, 9932, 13728, 11187, 1025, 2028, 1997, 2029, 1045, 2572, 13047, 2000, 1012, 1012, 2061, 2006, 2327, 1997, 2026, 1000, 12677, 1000, 2000, 2026, 24067, 1012, 1012, 1045, 2572, 2085, 1042, 1005, 1050, 5191, 2055, 2026, 2540, 1012, 1045, 2079, 4148, 2000, 2031, 1037, 3558, 1999, 4466, 2847, 1012, 102, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [19]:
checkpoint = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)

def tokenize_function(example):
    return tokenizer(example["title"], example["body"], truncation=True)


tokenized_datasets = raw_datasets.map(tokenize_function, batched=True)

data_collator = DataCollatorWithPadding(tokenizer=tokenizer, return_tensors="tf")

tf_train_dataset = tokenized_datasets["train"].to_tf_dataset(
    columns=["attention_mask", "input_ids", "token_type_ids"],
    label_cols=["labels"],
    shuffle=True,
    collate_fn=data_collator,
    batch_size=8,
)

tf_validation_dataset = tokenized_datasets["validation"].to_tf_dataset(
    columns=["attention_mask", "input_ids", "token_type_ids"],
    label_cols=["labels"],
    shuffle=False,
    collate_fn=data_collator,
    batch_size=8,
)

  0%|          | 0/152 [00:00<?, ?ba/s]

TypeError: ignored

In [16]:
from datasets import load_dataset
from transformers import AutoTokenizer, DataCollatorWithPadding
import numpy as np

raw_datasets = load_dataset("glue", "mrpc")
raw_datasets

  0%|          | 0/3 [00:00<?, ?it/s]

DatasetDict({
    train: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx'],
        num_rows: 3668
    })
    validation: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx'],
        num_rows: 408
    })
    test: Dataset({
        features: ['sentence1', 'sentence2', 'label', 'idx'],
        num_rows: 1725
    })
})

In [14]:
from datasets import load_dataset
from transformers import AutoTokenizer, DataCollatorWithPadding
import numpy as np

raw_datasets = load_dataset("glue", "mrpc")
checkpoint = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)


def tokenize_function(example):
    return tokenizer(example["sentence1"], example["sentence2"], truncation=True)


tokenized_datasets = raw_datasets.map(tokenize_function, batched=True)

data_collator = DataCollatorWithPadding(tokenizer=tokenizer, return_tensors="tf")

tf_train_dataset = tokenized_datasets["train"].to_tf_dataset(
    columns=["attention_mask", "input_ids", "token_type_ids"],
    label_cols=["labels"],
    shuffle=True,
    collate_fn=data_collator,
    batch_size=8,
)

tf_validation_dataset = tokenized_datasets["validation"].to_tf_dataset(
    columns=["attention_mask", "input_ids", "token_type_ids"],
    label_cols=["labels"],
    shuffle=False,
    collate_fn=data_collator,
    batch_size=8,
)

Generating train split:   0%|          | 0/3668 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/408 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1725 [00:00<?, ? examples/s]

Dataset glue downloaded and prepared to /root/.cache/huggingface/datasets/glue/mrpc/1.0.0/dacbe3125aa31d7f70367a07a8a9e72a5a0bfeb5fc42e75c9db75b96da6053ad. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

In [3]:
from transformers import TFAutoModelForSequenceClassification

model = TFAutoModelForSequenceClassification.from_pretrained(checkpoint, num_labels=2)

All model checkpoint layers were used when initializing TFBertForSequenceClassification.

Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [4]:
from tensorflow.keras.losses import SparseCategoricalCrossentropy

model.compile(
    optimizer="adam",
    loss=SparseCategoricalCrossentropy(from_logits=True),
    metrics=["accuracy"],
)
model.fit(
    tf_train_dataset,
    validation_data=tf_validation_dataset,
)

459/459 [==============================] - 96s 165ms/step - loss: 0.6579 - accuracy: 0.6562 - val_loss: 0.6240 - val_accuracy: 0.6838


In [5]:
from tensorflow.keras.optimizers.schedules import PolynomialDecay

batch_size = 8
num_epochs = 3
# The number of training steps is the number of samples in the dataset, divided by the batch size then multiplied
# by the total number of epochs. Note that the tf_train_dataset here is a batched tf.data.Dataset,
# not the original Hugging Face Dataset, so its len() is already num_samples // batch_size.
num_train_steps = len(tf_train_dataset) * num_epochs
lr_scheduler = PolynomialDecay(
    initial_learning_rate=5e-5, end_learning_rate=0.0, decay_steps=num_train_steps
)
from tensorflow.keras.optimizers import Adam

opt = Adam(learning_rate=lr_scheduler)

In [6]:
import tensorflow as tf

model = TFAutoModelForSequenceClassification.from_pretrained(checkpoint, num_labels=2)
loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
model.compile(optimizer=opt, loss=loss, metrics=["accuracy"])

All model checkpoint layers were used when initializing TFBertForSequenceClassification.

Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [7]:
model.fit(tf_train_dataset, validation_data=tf_validation_dataset, epochs=3)

Epoch 1/3
459/459 [==============================] - 91s 165ms/step - loss: 0.6369 - accuracy: 0.6698 - val_loss: 0.6312 - val_accuracy: 0.6838
Epoch 2/3
459/459 [==============================] - 73s 159ms/step - loss: 0.6347 - accuracy: 0.6745 - val_loss: 0.6238 - val_accuracy: 0.6838
Epoch 3/3
459/459 [==============================] - 73s 159ms/step - loss: 0.6174 - accuracy: 0.6745 - val_loss: 0.5697 - val_accuracy: 0.6838


In [8]:
preds = model.predict(tf_validation_dataset)["logits"]

In [9]:
class_preds = np.argmax(preds, axis=1)
print(preds.shape, class_preds.shape)

(408, 2) (408,)


In [10]:
import evaluate

metric = evaluate.load("glue", "mrpc")
metric.compute(predictions=class_preds, references=raw_datasets["validation"]["label"])

{'accuracy': 0.6838235294117647, 'f1': 0.8122270742358079}